In [40]:
import numpy as np       #importing pandas,numpy libraires & sqlite package
import pandas as pd
import sqlite3
df=pd.read_csv("adult.csv",sep=",")     #reading data
df.columns=['age','workclass','fnlwgt','education','education_num','marital_status','occupation'
                   ,'relationship','race','sex','capital_gain','capital_loss','hours_per_week','native_country','class']
df.head() #printing top 5 rows

age          workclass  fnlwgt   education  education_num  \
0   50   Self-emp-not-inc   83311   Bachelors             13   
1   38            Private  215646     HS-grad              9   
2   53            Private  234721        11th              7   
3   28            Private  338409   Bachelors             13   
4   37            Private  284582     Masters             14   

        marital_status          occupation    relationship    race      sex  \
0   Married-civ-spouse     Exec-managerial         Husband   White     Male   
1             Divorced   Handlers-cleaners   Not-in-family   White     Male   
2   Married-civ-spouse   Handlers-cleaners         Husband   Black     Male   
3   Married-civ-spouse      Prof-specialty            Wife   Black   Female   
4   Married-civ-spouse     Exec-managerial            Wife   White   Female   

   capital_gain  capital_loss  hours_per_week  native_country   class  
0             0             0              13   United-States   <=50K  
1             0             0              40   United-States   <=50K  
2             0             0              40   United-States   <=50K  
3             0             0              40            Cuba   <=50K  
4             0             0              40   United-States   <=50K

In [42]:
conn = sqlite3.connect('sqladb2.db')     #setting up database connection
cur = conn.cursor()  #getting cursor from connection
#query to create table
cur.execute("""create table adult(                  
             id INTEGER Primary key AUTOINCREMENT,
             age int,
             workclass VARCHAR(50),
             fnlwgt int,
             education VARCHAR(50),
             education_num int,
             marital_status VARCHAR(50),
             occupation VARCHAR(50),
             relationship VARCHAR(50),
             race VARCHAR(20),
             sex VARCHAR(20),
             capital_gain int,
             capital_loss int,
             hours_per_week int,
             native_country VARCHAR(30),
             class VARCHAR(30)      
        );""")

In [ ]:
#template of insert query
sql=" insert into adult values (%d, '%d', '%s', '%d', '%s','%d', '%s', '%s', '%s', '%s', '%s','%d', '%d', '%d', '%s', '%s'); "

#for loop to put values from df to corresponding location in template & insertion in table
for i in range(len(df)):
    cur.execute(sql % (i,df['age'][i],df['workclass'][i][1:],df['fnlwgt'][i],df['education'][i][1:],df['education_num'][i],
                       df['marital_status'][i][1:],df['occupation'][i][1:],df['relationship'][i][1:],df['race'][i][1:],df['sex'][i][1:],
                       df['capital_gain'][i],df['capital_loss'][i],df['hours_per_week'][i],df['native_country'][i][1:]
                       ,df['class'][i][1:]))
    
conn.commit() # saving the changes permanently in memory

In [44]:
#1 selecting 10 rows from table adult in database
cur.execute("""
            select * from adult limit 10;
         """)
for row in cur.fetchall():
    print(row)

(0, 50, 'Self-emp-not-inc', 83311, 'Bachelors', 13, 'Married-civ-spouse', 'Exec-managerial', 'Husband', 'White', 'Male', 0, 0, 13, 'United-States', '<=50K')
(1, 38, 'Private', 215646, 'HS-grad', 9, 'Divorced', 'Handlers-cleaners', 'Not-in-family', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K')
(2, 53, 'Private', 234721, '11th', 7, 'Married-civ-spouse', 'Handlers-cleaners', 'Husband', 'Black', 'Male', 0, 0, 40, 'United-States', '<=50K')
(3, 28, 'Private', 338409, 'Bachelors', 13, 'Married-civ-spouse', 'Prof-specialty', 'Wife', 'Black', 'Female', 0, 0, 40, 'Cuba', '<=50K')
(4, 37, 'Private', 284582, 'Masters', 14, 'Married-civ-spouse', 'Exec-managerial', 'Wife', 'White', 'Female', 0, 0, 40, 'United-States', '<=50K')
(5, 49, 'Private', 160187, '9th', 5, 'Married-spouse-absent', 'Other-service', 'Not-in-family', 'Black', 'Female', 0, 0, 16, 'Jamaica', '<=50K')
(6, 52, 'Self-emp-not-inc', 209642, 'HS-grad', 9, 'Married-civ-spouse', 'Exec-managerial', 'Husband', 'White', 'Male', 0, 0, 

In [47]:
#2 Showing average hours per week of all men working in private sector
cur.execute("""
            select avg(hours_per_week) from adult where workclass='Private' and sex='Male'; 
         """)
cur.fetchall()[0][0] #fetching values of query

42.22122591006424

In [48]:
#3 frequency table for education
cur.execute("""
            select education,count(id) from adult group by education; 
         """)

print("%20s %10s" %("education","Frequency"))
for row in cur.fetchall():  # printing values of frequency along with education category
    print("%20s %10d" %(row[0],row[1])) 
# frequency table for occupation
print(100*"-")
cur.execute("""
            select occupation,count(id) from adult group by occupation;
         """)
print("%20s %10s" %("occupation","Frequency")) 
for row in cur.fetchall():  # printing value of frequency along with occupation category
    print("%20s %10d" %(row[0],row[1]))
    
# frequency table for relationship
print(100*"-")
cur.execute("""
            select relationship,count(id) from adult group by relationship;
         """)
print("%20s %10s" %("relationship","Frequency"))
for row in cur.fetchall():  # printing value of frequency along with relationship category
    print("%20s %10d" %(row[0],row[1]))

           education  Frequency
                10th        933
                11th       1175
                12th        433
             1st-4th        168
             5th-6th        333
             7th-8th        646
                 9th        514
          Assoc-acdm       1067
           Assoc-voc       1382
           Bachelors       5354
           Doctorate        413
             HS-grad      10501
             Masters       1723
           Preschool         51
         Prof-school        576
        Some-college       7291
----------------------------------------------------------------------------------------------------
          occupation  Frequency
                   ?       1843
        Adm-clerical       3769
        Armed-Forces          9
        Craft-repair       4099
     Exec-managerial       4066
     Farming-fishing        994
   Handlers-cleaners       1370
   Machine-op-inspct       2002
       Other-service       3295
     Priv-house-serv        149
   

In [49]:
#4 Finding people who are married, working in private sector and having a masters degree
cur.execute("""
            select id,marital_status,workclass,education from adult where marital_status in('Married-AF-spouse',
            'Married-civ-spouse','Married-spouse-absent') and workclass=='Private' and
            education=='Masters';
         """)
print("%10s %25s %10s %10s" %('id','marital_status','workclass','education'))
for row in cur.fetchall(): #printing ('id','marital_status','workclass','education') for selected query
    print("%10d %25s %10s %10s" %(row[0],row[1],row[2],row[3]))

        id            marital_status  workclass  education
         4        Married-civ-spouse    Private    Masters
        86        Married-civ-spouse    Private    Masters
        99        Married-civ-spouse    Private    Masters
       187        Married-civ-spouse    Private    Masters
       197        Married-civ-spouse    Private    Masters
       310        Married-civ-spouse    Private    Masters
       360        Married-civ-spouse    Private    Masters
       404        Married-civ-spouse    Private    Masters
       434        Married-civ-spouse    Private    Masters
       467        Married-civ-spouse    Private    Masters
       605        Married-civ-spouse    Private    Masters
       696        Married-civ-spouse    Private    Masters
       776        Married-civ-spouse    Private    Masters
       894        Married-civ-spouse    Private    Masters
       915        Married-civ-spouse    Private    Masters
       926        Married-civ-spouse    Private    Maste

In [50]:
#5 average, minimum and maximum age group for people working in different sectors
# using aggregate function along with group by clause
cur.execute("""
            select workclass,avg(age),min(age),max(age) from adult group by workclass;
         """)
print("%20s %10s %10s %10s" %('sector','avg_age','min_age','max_age'))

for row in cur.fetchall(): # printing ('sector','avg_age','min_age','max_age') sector-wise
    print("%20s %10d %10d %10d" %(row[0],row[1],row[2],row[3]))

              sector    avg_age    min_age    max_age
                   ?         40         17         90
         Federal-gov         42         17         90
           Local-gov         41         17         90
        Never-worked         20         17         30
             Private         36         17         90
        Self-emp-inc         46         17         84
    Self-emp-not-inc         44         17         90
           State-gov         39         17         81
         Without-pay         47         19         72


In [51]:
#6 Calculating age distribution by country
#query which is used has agrregate function along with the groupby clause
cur.execute("""
            select native_country,avg(age),min(age),max(age) from adult group by native_country;
         """)
print("%30s %10s %10s %10s" %('native_country','avg_age','min_age','max_age'))
for row in cur.fetchall(): # printing ('native_country','avg_age','min_age','max_age') native-country wise
    print("%30s %10d %10d %10d" %(row[0],row[1],row[2],row[3]))

                native_country    avg_age    min_age    max_age
                             ?         38         17         90
                      Cambodia         37         18         65
                        Canada         42         17         80
                         China         42         22         75
                      Columbia         39         18         75
                          Cuba         45         21         82
            Dominican-Republic         37         18         78
                       Ecuador         36         21         90
                   El-Salvador         34         17         79
                       England         41         17         90
                        France         38         20         64
                       Germany         39         18         74
                        Greece         46         22         65
                     Guatemala         32         19         66
                         Haiti         3

In [52]:
#7 altering the table and adding a new column Net_Capital_Gain 
cur.execute("""
              ALTER TABLE adult ADD COLUMN Net_Capital_Gain int AFTER capital_loss;
             """)
conn.commit() #commiting connection permenantly in memory

In [53]:
#updating adult table set value of Net_Capital_Gain = capital_gain - capital_loss
cur.execute("UPDATE adult SET Net_Capital_Gain = capital_gain - capital_loss") 
cur.fetchall()

[]

In [54]:
cur.execute("select * from adult") # selecting all tuples from adult table
for row in cur.fetchall(): #printing all tuples
    print(row)

(0, 50, 'Self-emp-not-inc', 83311, 'Bachelors', 13, 'Married-civ-spouse', 'Exec-managerial', 'Husband', 'White', 'Male', 0, 0, 13, 'United-States', '<=50K', 0)
(1, 38, 'Private', 215646, 'HS-grad', 9, 'Divorced', 'Handlers-cleaners', 'Not-in-family', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(2, 53, 'Private', 234721, '11th', 7, 'Married-civ-spouse', 'Handlers-cleaners', 'Husband', 'Black', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(3, 28, 'Private', 338409, 'Bachelors', 13, 'Married-civ-spouse', 'Prof-specialty', 'Wife', 'Black', 'Female', 0, 0, 40, 'Cuba', '<=50K', 0)
(4, 37, 'Private', 284582, 'Masters', 14, 'Married-civ-spouse', 'Exec-managerial', 'Wife', 'White', 'Female', 0, 0, 40, 'United-States', '<=50K', 0)
(5, 49, 'Private', 160187, '9th', 5, 'Married-spouse-absent', 'Other-service', 'Not-in-family', 'Black', 'Female', 0, 0, 16, 'Jamaica', '<=50K', 0)
(6, 52, 'Self-emp-not-inc', 209642, 'HS-grad', 9, 'Married-civ-spouse', 'Exec-managerial', 'Husband', 'Whit

(1211, 31, 'Private', 32406, 'Some-college', 10, 'Divorced', 'Craft-repair', 'Unmarried', 'White', 'Female', 0, 0, 20, 'United-States', '<=50K', 0)
(1212, 54, 'Private', 99185, 'Doctorate', 16, 'Married-civ-spouse', 'Prof-specialty', 'Husband', 'White', 'Male', 15024, 0, 45, 'United-States', '>50K', 15024)
(1213, 20, 'Private', 205839, 'Some-college', 10, 'Never-married', 'Other-service', 'Own-child', 'White', 'Male', 0, 0, 16, 'United-States', '<=50K', 0)
(1214, 63, '?', 150389, 'Bachelors', 13, 'Widowed', '?', 'Not-in-family', 'White', 'Female', 0, 0, 40, 'United-States', '>50K', 0)
(1215, 48, 'Self-emp-not-inc', 243631, 'Some-college', 10, 'Married-civ-spouse', 'Craft-repair', 'Husband', 'Amer-Indian-Eskimo', 'Male', 7688, 0, 40, 'United-States', '>50K', 7688)
(1216, 33, '?', 163003, 'HS-grad', 9, 'Divorced', '?', 'Not-in-family', 'Asian-Pac-Islander', 'Female', 0, 0, 41, 'China', '<=50K', 0)
(1217, 31, 'Private', 231263, 'Bachelors', 13, 'Divorced', 'Exec-managerial', 'Not-in-famil

(2210, 27, 'Private', 158156, 'HS-grad', 9, 'Never-married', 'Other-service', 'Not-in-family', 'White', 'Female', 0, 0, 42, 'United-States', '<=50K', 0)
(2211, 42, 'Private', 70055, 'HS-grad', 9, 'Married-civ-spouse', 'Handlers-cleaners', 'Husband', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(2212, 60, '?', 131852, '5th-6th', 3, 'Married-civ-spouse', '?', 'Husband', 'White', 'Male', 0, 0, 30, 'United-States', '>50K', 0)
(2213, 64, 'Self-emp-not-inc', 177825, 'HS-grad', 9, 'Never-married', 'Other-service', 'Not-in-family', 'White', 'Male', 1055, 0, 40, 'United-States', '<=50K', 1055)
(2214, 33, 'Private', 127215, 'Some-college', 10, 'Married-civ-spouse', 'Sales', 'Husband', 'White', 'Male', 0, 0, 48, 'United-States', '>50K', 0)
(2215, 23, 'Private', 175183, 'Some-college', 10, 'Never-married', 'Adm-clerical', 'Not-in-family', 'White', 'Female', 0, 0, 40, 'United-States', '<=50K', 0)
(2216, 45, 'Private', 142287, 'Masters', 14, 'Married-civ-spouse', 'Exec-managerial', 'Husba

(3030, 31, 'Private', 327825, 'HS-grad', 9, 'Separated', 'Machine-op-inspct', 'Unmarried', 'White', 'Female', 0, 2238, 40, 'United-States', '<=50K', -2238)
(3031, 47, 'Private', 125892, 'Some-college', 10, 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', 0, 0, 75, 'United-States', '>50K', 0)
(3032, 40, '?', 78255, 'HS-grad', 9, 'Divorced', '?', 'Not-in-family', 'White', 'Male', 0, 0, 25, 'United-States', '<=50K', 0)
(3033, 30, 'Private', 398827, 'HS-grad', 9, 'Married-AF-spouse', 'Adm-clerical', 'Husband', 'White', 'Male', 0, 0, 60, 'United-States', '<=50K', 0)
(3034, 61, 'Private', 208919, 'Masters', 14, 'Married-civ-spouse', 'Sales', 'Husband', 'White', 'Male', 0, 0, 60, 'United-States', '>50K', 0)
(3035, 71, 'Local-gov', 365996, 'Bachelors', 13, 'Widowed', 'Prof-specialty', 'Unmarried', 'White', 'Female', 0, 0, 6, 'United-States', '<=50K', 0)
(3036, 42, 'Private', 307638, 'HS-grad', 9, 'Divorced', 'Adm-clerical', 'Own-child', 'White', 'Female', 0, 0, 40, 'United-Sta

(3709, 27, 'Private', 406662, 'HS-grad', 9, 'Never-married', 'Adm-clerical', 'Not-in-family', 'White', 'Male', 4416, 0, 40, 'United-States', '<=50K', 4416)
(3710, 42, 'Self-emp-not-inc', 37618, 'Some-college', 10, 'Married-civ-spouse', 'Farming-fishing', 'Husband', 'White', 'Male', 0, 0, 60, 'United-States', '<=50K', 0)
(3711, 27, 'Private', 114158, 'Assoc-voc', 11, 'Never-married', 'Adm-clerical', 'Own-child', 'White', 'Female', 0, 0, 35, 'United-States', '<=50K', 0)
(3712, 41, 'Private', 115562, 'HS-grad', 9, 'Divorced', 'Protective-serv', 'Own-child', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(3713, 32, 'Private', 353994, 'Bachelors', 13, 'Married-civ-spouse', 'Exec-managerial', 'Other-relative', 'Asian-Pac-Islander', 'Female', 0, 0, 40, 'China', '>50K', 0)
(3714, 21, 'Private', 344891, 'Some-college', 10, 'Never-married', 'Adm-clerical', 'Own-child', 'Asian-Pac-Islander', 'Male', 0, 0, 20, 'United-States', '<=50K', 0)
(3715, 44, 'Private', 286750, 'Bachelors', 13, 'Ma

...

(28193, 27, '?', 133359, 'Bachelors', 13, 'Married-spouse-absent', '?', 'Not-in-family', 'White', 'Male', 0, 0, 50, '?', '<=50K', 0)
(28194, 28, 'Private', 226891, 'Some-college', 10, 'Never-married', 'Adm-clerical', 'Unmarried', 'Asian-Pac-Islander', 'Female', 0, 0, 30, '?', '<=50K', 0)
(28195, 32, 'Private', 201988, 'Prof-school', 15, 'Married-civ-spouse', 'Sales', 'Husband', 'White', 'Male', 4508, 0, 40, '?', '<=50K', 4508)
(28196, 40, 'Private', 287008, 'Prof-school', 15, 'Married-civ-spouse', 'Prof-specialty', 'Husband', 'White', 'Male', 15024, 0, 55, 'Germany', '>50K', 15024)
(28197, 23, 'Private', 151910, 'Bachelors', 13, 'Never-married', 'Machine-op-inspct', 'Own-child', 'White', 'Female', 0, 1719, 40, 'United-States', '<=50K', -1719)
(28198, 25, 'Private', 231714, 'Some-college', 10, 'Married-civ-spouse', 'Machine-op-inspct', 'Husband', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(28199, 44, 'Self-emp-inc', 178510, 'Some-college', 10, 'Never-married', 'Sales', 'Not

(29193, 39, 'Self-emp-not-inc', 55568, 'Bachelors', 13, 'Married-civ-spouse', 'Farming-fishing', 'Wife', 'White', 'Female', 0, 0, 50, 'United-States', '<=50K', 0)
(29194, 48, 'Private', 155509, 'HS-grad', 9, 'Never-married', 'Adm-clerical', 'Not-in-family', 'Black', 'Female', 0, 0, 16, 'Trinadad&Tobago', '<=50K', 0)
(29195, 19, 'Private', 201178, 'HS-grad', 9, 'Never-married', 'Sales', 'Not-in-family', 'White', 'Female', 0, 0, 30, 'United-States', '<=50K', 0)
(29196, 27, 'Private', 37250, 'Some-college', 10, 'Married-civ-spouse', 'Machine-op-inspct', 'Husband', 'White', 'Male', 0, 1651, 40, 'United-States', '<=50K', -1651)
(29197, 59, 'Private', 314149, 'Assoc-voc', 11, 'Married-civ-spouse', 'Sales', 'Husband', 'White', 'Male', 0, 1740, 50, 'United-States', '<=50K', -1740)
(29198, 19, 'Private', 264593, 'Some-college', 10, 'Never-married', 'Sales', 'Other-relative', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(29199, 32, 'Private', 159589, 'HS-grad', 9, 'Never-married', 'Ha

(30192, 20, 'Private', 332931, 'Some-college', 10, 'Never-married', 'Other-service', 'Own-child', 'White', 'Female', 0, 0, 40, 'United-States', '<=50K', 0)
(30193, 66, 'Self-emp-inc', 76212, 'HS-grad', 9, 'Married-civ-spouse', 'Transport-moving', 'Husband', 'White', 'Male', 0, 0, 50, 'United-States', '>50K', 0)
(30194, 31, 'Private', 301168, 'Some-college', 10, 'Never-married', 'Craft-repair', 'Not-in-family', 'White', 'Male', 0, 0, 40, 'Italy', '<=50K', 0)
(30195, 22, 'Private', 440969, 'Some-college', 10, 'Never-married', 'Other-service', 'Own-child', 'White', 'Female', 0, 0, 24, 'United-States', '<=50K', 0)
(30196, 32, 'Private', 154950, 'Prof-school', 15, 'Never-married', 'Prof-specialty', 'Not-in-family', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(30197, 23, 'Private', 218343, 'Assoc-acdm', 12, 'Never-married', 'Sales', 'Own-child', 'White', 'Female', 0, 0, 40, 'United-States', '<=50K', 0)
(30198, 21, 'Private', 239577, 'Some-college', 10, 'Never-married', 'Adm-cleri

(31192, 19, '?', 230874, 'Some-college', 10, 'Never-married', '?', 'Own-child', 'White', 'Female', 0, 0, 40, 'United-States', '<=50K', 0)
(31193, 59, 'Self-emp-not-inc', 148526, 'Some-college', 10, 'Married-civ-spouse', 'Sales', 'Husband', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(31194, 36, 'Private', 160192, 'HS-grad', 9, 'Never-married', 'Other-service', 'Not-in-family', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(31195, 50, 'Local-gov', 74660, 'Some-college', 10, 'Widowed', 'Prof-specialty', 'Unmarried', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(31196, 60, 'Self-emp-inc', 142494, '10th', 6, 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', 0, 0, 40, 'United-States', '<=50K', 0)
(31197, 30, 'Private', 122042, 'Masters', 14, 'Married-civ-spouse', 'Exec-managerial', 'Husband', 'White', 'Male', 0, 0, 45, 'United-States', '>50K', 0)
(31198, 28, 'Self-emp-inc', 37088, 'Bachelors', 13, 'Never-married', 'Sales', 'Not-in-family', 'W

(32191, 64, 'State-gov', 104361, 'Some-college', 10, 'Separated', 'Adm-clerical', 'Not-in-family', 'White', 'Female', 0, 0, 65, 'United-States', '<=50K', 0)
(32192, 68, 'Private', 274096, '10th', 6, 'Divorced', 'Transport-moving', 'Not-in-family', 'White', 'Male', 0, 0, 20, 'United-States', '<=50K', 0)
(32193, 42, 'State-gov', 455553, 'HS-grad', 9, 'Never-married', 'Adm-clerical', 'Unmarried', 'Black', 'Female', 0, 0, 40, 'United-States', '<=50K', 0)
(32194, 41, 'Private', 112283, 'HS-grad', 9, 'Married-civ-spouse', 'Craft-repair', 'Husband', 'White', 'Male', 0, 0, 60, 'United-States', '>50K', 0)
(32195, 41, 'Self-emp-inc', 64506, 'HS-grad', 9, 'Married-civ-spouse', 'Farming-fishing', 'Husband', 'White', 'Male', 0, 0, 50, 'United-States', '<=50K', 0)
(32196, 22, 'State-gov', 24395, 'Some-college', 10, 'Married-civ-spouse', 'Adm-clerical', 'Wife', 'White', 'Female', 0, 0, 20, 'United-States', '<=50K', 0)
(32197, 67, 'Self-emp-inc', 182581, 'Some-college', 10, 'Married-civ-spouse', 'Exec